## The Deepnote Notebook
The most important part of Deepnote is the notebook. This is where the magic happens: it's where you read, analyze, and visualize your data.

#### Do EDA on the dataset for ease of operations.

In [4]:
!git clone https://github.com/thunlp/OpenNRE.git
# !cd OpenNRE/
# !pip install -r OpenNRE/requirements.txt
!python OpenNRE/setup.py install

'git' is not recognized as an internal or external command,
operable program or batch file.


running install
running bdist_egg
running egg_info
writing opennre.egg-info\PKG-INFO
writing dependency_links to opennre.egg-info\dependency_links.txt
writing top-level names to opennre.egg-info\top_level.txt
reading manifest file 'opennre.egg-info\SOURCES.txt'
writing manifest file 'opennre.egg-info\SOURCES.txt'
installing library code to build\bdist.win-amd64\egg
running install_lib
creating build\bdist.win-amd64\egg
creating build\bdist.win-amd64\egg\EGG-INFO
copying opennre.egg-info\PKG-INFO -> build\bdist.win-amd64\egg\EGG-INFO
copying opennre.egg-info\SOURCES.txt -> build\bdist.win-amd64\egg\EGG-INFO
copying opennre.egg-info\dependency_links.txt -> build\bdist.win-amd64\egg\EGG-INFO
copying opennre.egg-info\top_level.txt -> build\bdist.win-amd64\egg\EGG-INFO
creating 'dist\opennre-0.1-py3.9.egg' and adding 'build\bdist.win-amd64\egg' to it
removing 'build\bdist.win-amd64\egg' (and everything under it)
Processing opennre-0.1-py3.9.egg
Removing c:\users\arifa\anaconda3\lib\site-pac


zip_safe flag not set; analyzing archive contents...


In [33]:
import json
import csv
import re
from pathlib import Path
# from opennre.module.nn import cnn
# import opennre
# f = open("dataverse_files/award.award_nominated_work.award_nominations..award.award_nomination.award_nominee.json")
# data = json.load(f)

#create a global variable to store input values temporarily
input_list = []

In [34]:
data_file_path = "dataverse_files/"
dirpath = Path(data_file_path)

# iterate through all files in dev directory
for file in dirpath.iterdir():
    file_path = f"{file}"
    if file_path.endswith('.json'):
        print(file_path)
        f = open(file_path)
        data = json.load(f)
        get_relations(data)

dataverse_files\award.award_nominated_work.award_nominations..award.award_nomination.award_nominee.json
dataverse_files\book.author.works_written.json
dataverse_files\education.educational_institution.students_graduates..education.educational_institution.students_graduates.json
dataverse_files\film.actor.film..film.performance.character.json
dataverse_files\film.film.language.json
dataverse_files\film.producer.film.json


In [4]:
# Create proposed model here.
# from torch import nn
# class ProposedModel(nn.Module):
#     def __init__(self):
#         self.cnn_module = 

#     def forward(x):
#         pass

In [31]:
# relation = data['data'][0]['relation']['name']
# print(relation)
# article_title = data['data'][0]['table']['context']['article']['title']
# article_abstract = data['data'][0]['table']['context']['article']['abstract']
# table_caption = data['data'][0]['table']['caption']
# table_section_title = data['data'][0]['table']['context']['section']['title']
# table_headers_dict = data['data'][0]['table']['headers'][0]['row']
def get_relations(data):

    all_table_row_values = []
    for i in range(500):#(len(data))
        #consider contextual information for each table
        relation = data['data'][i]['relation']['name']
        subject_col = data['data'][i]['relation']['subj column']
        object_col = data['data'][i]['relation']['obj column']
        article_title = data['data'][i]['table']['context']['article']['title']
    #     article_abstract = data['data'][i]['table']['context']['article']['abstract']
        if 'caption' in data['data'][i]['table'].keys():
            table_caption = data['data'][i]['table']['caption']
        else:
            table_caption = ""
        table_section_title = data['data'][i]['table']['context']['section']['title']
        table_headers_dict = data['data'][i]['table']['headers'][0]['row']

        # For the elements in the table.
        table_values_list = data['data'][i]['table']['rows']
        table_row_values = []
        for table_value in table_values_list:
            # Each table_value is a dict.
            cells = table_value['row']['cells']  # 'cells' is a list.
            cells_list = [cell['value'] for cell in cells]
            table_row_values.append(cells_list)

        #taking header values
        subject_header = ""
        object_header = ""
        header_values_dict = data['data'][i]['table']['headers'][0]
        cells = header_values_dict['row']['cells']
        if subject_col != -1:
            for cell in cells: 
                if int(cell['number']) == int(subject_col):
                    subject_header = cell['value']
        if object_col != -1:
            for cell in cells: 
                if int(cell['number']) == int(object_col):
                    object_header = cell['value']
        
        if subject_col !=-1 and object_col != -1:
            headers = subject_header + ' ' + object_header
        else:
            headers = subject_header + object_header
            
        #consider entity pairs for each table
        #considering relation between article title and cell values
        pattern = re.compile('[\W_]+')
        table_values_list = data['data'][i]['table']['rows']
        if subject_col == -1:
            for table_value in table_values_list:
                cells = table_value['row']['cells']
                for cell in cells:
                    if int(cell['number']) == int(object_col):
    #                     print('entered')
                        current_input = []
                        subject_entity = article_title
                        object_entity = cell['value']
                        #using regex to remove non-alpha numeric characters
                        object_entity = pattern.sub(' ', object_entity)
                        current_input.extend((table_caption, table_section_title, headers, subject_entity + ' ' + object_entity, relation))
#                         print(current_input)
                        input_list.append(current_input)

        elif object_col == -1:
            for table_value in table_values_list:
                cells = table_value['row']['cells']
                for cell in cells:
                    if int(cell['number']) == int(subject_col):
    #                     print('entered')
                        current_input = []
                        object_entity = article_title
                        subject_entity = cell['value']
                        #using regex to remove non-alpha numeric characters
                        subject_entity = pattern.sub(' ', subject_entity)
                        current_input.extend((table_caption, table_section_title, headers, subject_entity + ' ' + object_entity, relation))
#                         print(current_input)
                        input_list.append(current_input)
        else:
            for table_value in table_values_list:
                cells = table_value['row']['cells']
                for cell in cells:
                    if int(cell['number']) == int(subject_col):
                        object_entity = article_title
                        subject_entity = cell['value']
                        #using regex to remove non-alpha numeric characters
                        subject_entity = pattern.sub(' ', subject_entity)
                    for second_cell in cells:
                        if int(cell['number']) == int(object_col):
                            current_input = []
                            object_entity = cell['value']
                            #using regex to remove non-alpha numeric characters
                            object_entity = pattern.sub(' ', object_entity)
                            current_input.extend((table_caption, table_section_title, headers, subject_entity + ' ' + object_entity, relation))
#                             print(current_input)
                            input_list.append(current_input)
    #consider entity pairs for each table
    #considering relation between article title and cell values
#     pattern = re.compile('[\W_]+')
#     if subject_col == -1:
#         for row in table_row_values:
#             try:
#                 current_input = []
#                 subject_entity = article_title
#                 object_entity = row[object_col]
#                 #using regex to remove non-alpha numeric characters
#                 object_entity = pattern.sub(' ', object_entity)
#                 current_input.extend((table_caption, table_section_title, subject_entity + ' ' + object_entity, relation))
#                 input_list.append(current_input)
#             except IndexError:
#                 pass
#     elif object_col == -1:
#          for row in table_row_values:
#             try:
#                 current_input = []
#                 subject_entity = row[subject_col]
#                 object_entity = article_title 
#                 #using regex to remove non-alpha numeric characters
#                 subject_entity = pattern.sub(' ', subject_entity)
#                 current_input.extend((table_caption, table_section_title, subject_entity + ' ' + object_entity, relation))
#                 input_list.append(current_input)
#             except IndexError:
#                 pass
#     #considering relation between different columns within same row
#     else:
#         for row in table_row_values:
#             try:
#                 current_input = []
#                 subject_entity = row[subject_col]
#                 object_entity = row[object_col]
#                 #using regex to remove non-alpha numeric characters
#                 subject_entity = pattern.sub(' ', subject_entity)
#                 object_entity = pattern.sub(' ', object_entity)
#                 current_input.extend((table_caption, table_section_title, subject_entity + ' ' + object_entity, relation))
#                 input_list.append(current_input) 
#             except IndexError:
#                 pass
                
#     for row in table_row_values:
#         #to filter out tables with just one columns
#         if(len(row)) > 2: 
#             #skip the first cell as it usually contins serial numbers of each row
#             for first_cell in row[1:]:
#                 for second_cell in row[1:]:
#                     current_input = []
#                     pattern = re.compile('[\W_]+')
#                     first_cell = pattern.sub(' ', first_cell)
#                     second_cell = pattern.sub(' ', second_cell)
#                     #consider only non-empty cell values and prevent pairing same cell contents twice
#                     if (first_cell and second_cell) and (first_cell != second_cell) :
#                         current_input.extend((table_caption, table_section_title, first_cell + ' ' + second_cell, relation))
#                         input_list.append(current_input)
#         for index in range(1, len(row)):
#             #skip the first cell as it usually contins serial numbers of each row
#             current_input = []
# #             print(article_title, row[index])
#             #append contents to temporary list
#             cell_value = pattern.sub(' ', row[index])
#             current_input.extend((table_caption, table_section_title, article_title + ' ' + cell_value, relation))
#             input_list.append(current_input)
            
        all_table_row_values.append(table_row_values)

In [35]:
# print(current_input)
for input_value in input_list[:5000]:
    print(input_value)

['Recipients', 'Recipients', 'Name of the recipient', 'Nishan-e-Haider  Saif Ali Janjua Saif Ali Janjua Hilal e Kashmir Hilal e Kashmir ', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee']
['Recipients', 'Recipients', 'Name of the recipient', 'Nishan-e-Haider  Raja Muhammad Sarwar Raja Muhammad Sarwar ', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee']
['Recipients', 'Recipients', 'Name of the recipient', 'Nishan-e-Haider  Tufail Mohammad Tufail Mohammad ', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee']
['Recipients', 'Recipients', 'Name of the recipient', 'Nishan-e-Haider  Raja Aziz Bhatti Raja Aziz Bhatti ', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee']
['Recipients', 'Recipients', 'Name of the recipient', 'Nishan-e-Haider  Rashid Minhas Rashid Minhas ', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nomin

['', 'Awards and nominations', 'Category Recipient', 'Most Popular Actor TV   Seo In guk Seo In guk ', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee']
['', 'Awards and nominations', 'Category Recipient', 'Most Popular Actor TV   So Ji sub So Ji sub ', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee']
['', 'Awards and nominations', 'Category Recipient', 'Most Popular Actress TV   Gong Hyo jin Gong Hyo jin ', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee']
['', 'Awards and nominations', 'Category Recipient', 'Most Popular Actress TV   Gong Hyo jin Gong Hyo jin ', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee']
['', 'Awards and nominations', 'Category Recipient', 'Outstanding Korean Drama Master s Sun', 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee']
['', 'Awards and nominations', 'Category Recipient', '

In [44]:
data

{'data': [{'relation': {'name': 'award.award_nominated_work.award_nominations..award.award_nomination.award_nominee',
    'obj column': 1,
    'pairs present': 6,
    'rows': 11,
    'subj column': -1},
   'table': {'caption': 'Recipients',
    'context': {'article': {'abstract': 'Nishan-e-Haider () (abbreviated as "NH") is [[Pakistan|Pakistan]]\'s highest [[military gallantry award|military decoration]]. "Nishan-e-Haider" literally means "Emblem of the Lion" in the [[Urdu|Urdu]] language. The word "Haider" is also the [[epithet|epithet]] of [[Ali|Ali]], who is referred to as the \'Lion of God\', a valiant warrior and leader.',
      'id': '377673',
      'title': 'Nishan-e-Haider',
      'type': 'military award <SEP>  Pakistan military medal with service ribbon<br>(Decoration)\n'},
     'ordinal': 1,
     'section': {'title': 'Recipients'}},
    'headers': [{'row': {'cells': [{'number': '0', 'value': '№'},
        {'number': '1', 'value': 'Name of the recipient'},
        {'number': '

In [38]:
def write_output_to_tsv(output_path):
  header = ['table_caption', 'table_section_title', 'headers','entity pair', 'relation']

  with open(output_path, 'w', newline='', encoding='UTF8') as f:
    writer = csv.writer(f, delimiter='\t')

    # write the header
    writer.writerow(header)

    # write the data
    for data in input_list:
      writer.writerow(data)

In [39]:
write_output_to_tsv("Processed Data\Input 2.tsv")

In [ ]:
cells_list

['11',
 '[[Lalak Jan|Lalak Jan]]',
 '12 Northern Light Infantry,[[Pakistan Army|Pakistan Army]]',
 '[[Havaldar|Havaldar]]',
 '[[Kargil War|Kargil War]]',
 '7 July 1999']

### Visualizing your data
Create charts for your data in one click by selecting **Chart** from the Block dropdown list.
<img src="media/chart.gif"></img>

<br>
<br>

## [Back](00_getting_started.ipynb)

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=9a16a70d-7aa0-47a1-a88f-8805562c8a00' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>